In [1]:
import pandas as pd
import numpy as np
from sklearn.model_selection import GridSearchCV
import onnxruntime as rt
import onnx
import xgboost as xgb
from skl2onnx.common.data_types import FloatTensorType
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_selection import SelectFromModel
from sklearn.metrics import accuracy_score, classification_report
from sklearn.pipeline import Pipeline
from skl2onnx import convert_sklearn
from scipy.stats import ks_2samp

C:\Users\alexd\AppData\Local\Temp\ipykernel_19336\4050468885.py:1: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd


# Model 1

In [45]:
# Modify the data files
train_data = pd.read_csv('data/train_data_1.csv')
test_data = pd.read_csv('data/test_data_1.csv')

y_train = train_data['checked']
X_train = train_data.drop(['checked'], axis=1)
X_train = X_train.astype(np.float32)

y_test = test_data['checked']
X_test = test_data.drop(['checked'], axis=1)
X_test = X_test.astype(np.float32)

In [46]:
# Select important features
selector = SelectFromModel(RandomForestClassifier(class_weight='balanced'))

In [47]:
# Use XGBoost as classifier
classifier = xgb.XGBClassifier(objective='binary:logistic')

In [48]:
# Create a pipeline object with our selector and classifier
pipeline = Pipeline(steps=[('feature_selection', selector), ('classification', classifier)])

In [49]:
# Cross-validate pipeline
# Define the parameter grid for grid search
param_grid = {
    'feature_selection__max_features': [50, 75, 100],
    'classification__learning_rate': [0.1, 0.2, 0.3],
}

# Create a GridSearchCV object with the pipeline and parameter grid
grid_search = GridSearchCV(pipeline, param_grid, scoring= 'roc_auc', cv=5, verbose= 2)

# Perform grid search with cross-validation
grid_search.fit(X_train, y_train)

# Print the best parameters found
print("Best Parameters:", grid_search.best_params_)

# Print the best cross-validation score
print("Best Cross-Validation Score:", grid_search.best_score_)

Fitting 5 folds for each of 9 candidates, totalling 45 fits
[CV] END classification__learning_rate=0.1, feature_selection__max_features=50; total time=   4.0s
[CV] END classification__learning_rate=0.1, feature_selection__max_features=50; total time=   3.3s
[CV] END classification__learning_rate=0.1, feature_selection__max_features=50; total time=   3.2s
[CV] END classification__learning_rate=0.1, feature_selection__max_features=50; total time=   3.2s
[CV] END classification__learning_rate=0.1, feature_selection__max_features=50; total time=   3.2s
[CV] END classification__learning_rate=0.1, feature_selection__max_features=75; total time=   3.2s
[CV] END classification__learning_rate=0.1, feature_selection__max_features=75; total time=   3.2s
[CV] END classification__learning_rate=0.1, feature_selection__max_features=75; total time=   3.2s
[CV] END classification__learning_rate=0.1, feature_selection__max_features=75; total time=   3.2s
[CV] END classification__learning_rate=0.1, featu

In [50]:
# Update pipeline
pipeline.named_steps['classification'].set_params(learning_rate= grid_search.best_params_['classification__learning_rate'])
pipeline.named_steps['feature_selection'].set_params(max_features= grid_search.best_params_['feature_selection__max_features'])

SelectFromModel(estimator=RandomForestClassifier(class_weight='balanced'),
                max_features=100)

In [51]:
model = pipeline
model.fit(X_train, y_train)

# Evaluate the model
y_pred = model.predict(X_test)
original_accuracy = accuracy_score(y_test, y_pred)
print(classification_report(y_test, y_pred))
print('Accuracy of the original model: ', original_accuracy)

              precision    recall  f1-score   support

           0       0.95      0.99      0.97      2278
           1       0.82      0.50      0.62       251

    accuracy                           0.94      2529
   macro avg       0.89      0.75      0.80      2529
weighted avg       0.94      0.94      0.93      2529

Accuracy of the original model:  0.9398971925662317


In [52]:
from skl2onnx import update_registered_converter
from skl2onnx.common.shape_calculator import calculate_linear_classifier_output_shapes  # noqa
from onnxmltools.convert.xgboost.operator_converters.XGBoost import convert_xgboost  # noqa

update_registered_converter(
    xgb.XGBClassifier,
    "XGBoostClassifier",
    calculate_linear_classifier_output_shapes,
    convert_xgboost,
    options={"nocl": [True, False], "zipmap": [True, False, "columns"]}
)
# Convert the model to ONNX
onnx_model = convert_sklearn(
    pipeline, initial_types=[('X', FloatTensorType((None, X_train.shape[1])))],
    target_opset=12)

# Check the accuracy of the converted model
sess = rt.InferenceSession(onnx_model.SerializeToString())
y_pred_onnx =  sess.run(None, {'X': X_test.values.astype(np.float32)})

accuracy_onnx_model = accuracy_score(y_test, y_pred_onnx[0])
print('Accuracy of the ONNX model: ', accuracy_onnx_model)

Accuracy of the ONNX model:  0.9398971925662317


In [2]:
# # Save the model
# onnx.save(onnx_model, "model/model_1.onnx")
# 
# # Load the model
# new_session = rt.InferenceSession("model/model_1.onnx")
# 
# # Predict the target
# y_pred_onnx2 =  new_session.run(None, {'X': X_test.values.astype(np.float32)})
# 
# accuracy_onnx_model = accuracy_score(y_test, y_pred_onnx2[0])
# print('Accuracy of the ONNX model: ', accuracy_onnx_model)
model = onnx.load("model/model_1.onnx")


# Giskard - BlackBox Testing Generation

In [5]:
%pip install onnx2torch
import giskard
import torch
from onnx2torch import convert
torch_model_1 = convert("model/model_1.onnx")
# Wrap your Pandas DataFrame with Giskard.Dataset (test set, a golden dataset, etc.).
giskard_dataset = giskard.Dataset(
    df=pd.read_csv('data/synth_data_for_training.csv'),  # A pandas.DataFrame that contains the raw data (before all the pre-processing steps) and the actual ground truth variable (target).
    target="checked",  # Ground truth variable
)

giskard_model = giskard.Model(
    model=torch_model_1,  # A prediction function that encapsulates all the data pre-processing steps and that could be executed with the dataset used by the scan.
    model_type="classification",  # Either regression, classification or text_generation.
    classification_labels=[0, 1],  # Their order MUST be identical to the prediction_function's output order
)

Note: you may need to restart the kernel to use updated packages.


PermissionError: [Errno 13] Permission denied: 'C:\\Users\\alexd\\PycharmProjects\\ModelTesting\\model\\tmprmwg0x5m'

In [55]:
scan_results = giskard.scan(giskard_model, giskard_dataset)

2024-03-21 20:25:38,359 pid:26128 MainThread giskard.datasets.base INFO     Casting dataframe columns from {'adres_aantal_brp_adres': 'int64', 'adres_aantal_verschillende_wijken': 'int64', 'adres_aantal_verzendadres': 'int64', 'adres_aantal_woonadres_handmatig': 'int64', 'adres_dagen_op_adres': 'int64', 'adres_recentst_onderdeel_rdam': 'int64', 'adres_recentste_buurt_groot_ijsselmonde': 'int64', 'adres_recentste_buurt_nieuwe_westen': 'int64', 'adres_recentste_buurt_other': 'int64', 'adres_recentste_buurt_oude_noorden': 'int64', 'adres_recentste_buurt_vreewijk': 'int64', 'adres_recentste_plaats_other': 'int64', 'adres_recentste_plaats_rotterdam': 'int64', 'adres_recentste_wijk_charlois': 'int64', 'adres_recentste_wijk_delfshaven': 'int64', 'adres_recentste_wijk_feijenoord': 'int64', 'adres_recentste_wijk_ijsselmonde': 'int64', 'adres_recentste_wijk_kralingen_c': 'int64', 'adres_recentste_wijk_noord': 'int64', 'adres_recentste_wijk_other': 'int64', 'adres_recentste_wijk_prins_alexa': 'in

C:\Users\alexd\.virtualenvs\ModelTesting-Rom7SsEP\Lib\site-packages\giskard\scanner\scanner.py:258: UserWarning: It looks like your dataset has a very large number of features (315), are you sure this is correct? The giskard.Dataset should be created from raw data *before* pre-processing (categorical encoding, vectorization, etc.). You can also limit the number of features to scan by setting the `features` argument. Check https://docs.giskard.ai/en/latest/guides/wrap_dataset/index.html for more details.
  warning(


2024-03-21 20:25:41,088 pid:26128 MainThread giskard.datasets.base INFO     Casting dataframe columns from {'adres_aantal_brp_adres': 'int64', 'adres_aantal_verschillende_wijken': 'int64', 'adres_aantal_verzendadres': 'int64', 'adres_aantal_woonadres_handmatig': 'int64', 'adres_dagen_op_adres': 'int64', 'adres_recentst_onderdeel_rdam': 'int64', 'adres_recentste_buurt_groot_ijsselmonde': 'int64', 'adres_recentste_buurt_nieuwe_westen': 'int64', 'adres_recentste_buurt_other': 'int64', 'adres_recentste_buurt_oude_noorden': 'int64', 'adres_recentste_buurt_vreewijk': 'int64', 'adres_recentste_plaats_other': 'int64', 'adres_recentste_plaats_rotterdam': 'int64', 'adres_recentste_wijk_charlois': 'int64', 'adres_recentste_wijk_delfshaven': 'int64', 'adres_recentste_wijk_feijenoord': 'int64', 'adres_recentste_wijk_ijsselmonde': 'int64', 'adres_recentste_wijk_kralingen_c': 'int64', 'adres_recentste_wijk_noord': 'int64', 'adres_recentste_wijk_other': 'int64', 'adres_recentste_wijk_prins_alexa': 'in

In [56]:
display(scan_results)

<iframe id="scan-2053472659728" srcdoc="<!doctype html>
<html lang="en">

<head>
 <title>Giskard Scan Results</title>
 <base target="_blank">
 <meta charset="utf-8">
 
<style>pre code.hljs{display:block;overflow-x:auto;padding:1em}code.hljs{padding:3px 5px}
/*!
 Theme: GitHub Dark
 Description: Dark theme as seen on github.com
 Author: github.com
 Maintainer: @Hirse
 Updated: 2021-05-15

 Outdated base version: https://github.com/primer/github-syntax-dark
 Current colors taken from GitHub's CSS
*/.hljs{background:#0d1117;color:#c9d1d9}.hljs-doctag,.hljs-keyword,.hljs-meta .hljs-keyword,.hljs-template-tag,.hljs-template-variable,.hljs-type,.hljs-variable.language_{color:#ff7b72}.hljs-title,.hljs-title.class_,.hljs-title.class_.inherited__,.hljs-title.function_{color:#d2a8ff}.hljs-attr,.hljs-attribute,.hljs-literal,.hljs-meta,.hljs-number,.hljs-operator,.hljs-selector-attr,.hljs-selector-class,.hljs-selector-id,.hljs-variable{color:#79c0ff}.hljs-meta .hljs-string,.hljs-regexp,.hljs-string{color:#a5d6ff}.hljs-built_in,.hljs-symbol{color:#ffa657}.hljs-code,.hljs-comment,.hljs-formula{color:#8b949e}.hljs-name,.hljs-quote,.hljs-selector-pseudo,.hljs-selector-tag{color:#7ee787}.hljs-subst{color:#c9d1d9}.hljs-section{color:#1f6feb;font-weight:700}.hljs-bullet{color:#f2cc60}.hljs-emphasis{color:#c9d1d9;font-style:italic}.hljs-strong{color:#c9d1d9;font-weight:700}.hljs-addition{background-color:#033a16;color:#aff5b4}.hljs-deletion{background-color:#67060c;color:#ffdcd7}.hljs-copy-wrapper{overflow:hidden;position:relative}.hljs-copy-button:focus,.hljs-copy-wrapper:hover .hljs-copy-button{transform:translateX(0)}.hljs-copy-button{background-color:#2d2b57;background-color:var(--hljs-theme-background);background-image:url('data:image/svg+xml;charset=utf-8,<svg xmlns="http://www.w3.org/2000/svg" width="16" height="16" fill="none" viewBox="0 0 24 24"><path fill="%23fff" fill-rule="evenodd" d="M6 5a1 1 0 0 0-1 1v14a1 1 0 0 0 1 1h12a1 1 0 0 0 1-1V6a1 1 0 0 0-1-1h-2a1 1 0 1 1 0-2h2a3 3 0 0 1 3 3v14a3 3 0 0 1-3 3H6a3 3 0 0 1-3-3V6a3 3 0 0 1 3-3h2a1 1 0 0 1 0 2H6Z" clip-rule="evenodd"/><path fill="%23fff" fill-rule="evenodd" d="M7 3a2 2 0 0 1 2-2h6a2 2 0 0 1 2 2v2a2 2 0 0 1-2 2H9a2 2 0 0 1-2-2V3Zm8 0H9v2h6V3Z" clip-rule="evenodd"/></svg>');background-position:50%;background-repeat:no-repeat;border:1px solid #ffffff22;border-radius:.25rem;color:#fff;height:2rem;position:absolute;right:1em;text-indent:-9999px;top:1em;transition:background-color .2s ease,transform .2s ease-out;width:2rem}.hljs-copy-button:hover{border-color:#ffffff44}.hljs-copy-button:active{border-color:#ffffff66}.hljs-copy-button[data-copied=true]{background-image:none;text-indent:0;width:auto}@media (prefers-reduced-motion){.hljs-copy-button{transition:none}}.hljs-copy-alert{clip:rect(0 0 0 0);-webkit-clip-path:inset(50%);clip-path:inset(50%);height:1px;overflow:hidden;position:absolute;white-space:nowrap;width:1px}
/*! tailwindcss v3.3.2 | MIT License | https://tailwindcss.com*/*,:after,:before{border:0 solid #e5e7eb;box-sizing:border-box}:after,:before{--tw-content:""}html{-webkit-text-size-adjust:100%;font-feature-settings:normal;font-family:ui-sans-serif,system-ui,-apple-system,BlinkMacSystemFont,Segoe UI,Roboto,Helvetica Neue,Arial,Noto Sans,sans-serif,Apple Color Emoji,Segoe UI Emoji,Segoe UI Symbol,Noto Color Emoji;font-variation-settings:normal;line-height:1.5;-moz-tab-size:4;-o-tab-size:4;tab-size:4}body{line-height:inherit;margin:0}hr{border-top-width:1px;color:inherit;height:0}abbr:where([title]){-webkit-text-decoration:underline dotted;text-decoration:underline dotted}h1,h2,h3,h4,h5,h6{font-size:inherit;font-weight:inherit}a{color:inherit;text-decoration:inherit}b,strong{font-weight:bolder}code,kbd,pre,samp{font-family:ui-monospace,SFMono-Regular,Menlo,Monaco,Consolas,Liberation Mono,Courier New,monospace;font-size:1em}small{font-size:80%}sub,sup{font-size:75%;line-height:0;position:relative;vertical-align:baseline}sub{bottom:-.25em}sup{top:-.5em}table{border-collapse:

# Demographic parity tests

## Gender Parity Test

In [57]:
gender_groups = X_test.groupby('persoon_geslacht_vrouw')

# Define a dictionary to map numeric values to gender labels
gender_labels = {0: 'Men', 1: 'Women'}

gender_risk_scores = {}
for gender, group in gender_groups:
    preds = model.predict(group)
    gender_label = gender_labels[gender]  
    gender_risk_scores[gender_label] = preds.mean()

print("\nGender Parity Test:")
print(gender_risk_scores)



Gender Parity Test:
{'Men': 0.06264150943396227, 'Women': 0.05813953488372093}


## Age Parity Test

In [58]:
age_groups = [18, 26, 36, 46, 56, 66]
age_data = []
for i in range(len(age_groups)-1):
    lower_bound = age_groups[i]
    upper_bound = age_groups[i+1]
    group = X_test[(X_test['persoon_leeftijd_bij_onderzoek'] >= lower_bound) & (X_test['persoon_leeftijd_bij_onderzoek'] < upper_bound)]
    age_data.append(group)

age_risk_scores = []
for group in age_data:
    preds = model.predict(group)
    age_risk_scores.append(preds.mean())

print("\nAge Parity Test:")
for i, group in enumerate(age_groups[:-1]):
    print(f"Age group {group}-{age_groups[i+1]}: Mean risk score = {age_risk_scores[i]}")



Age Parity Test:
Age group 18-26: Mean risk score = 0.2413793103448276
Age group 26-36: Mean risk score = 0.17410714285714285
Age group 36-46: Mean risk score = 0.1076158940397351
Age group 46-56: Mean risk score = 0.03273495248152059
Age group 56-66: Mean risk score = 0.010526315789473684


## "Other comments" Parity Test

In [59]:
# Group by 'adres_aantal_brp_adres'
adres_groups = X_test.groupby('typering_other')

adres_risk_scores = {}
for adres, group in adres_groups:
    preds = model.predict(group)
    adres_risk_scores[adres] = preds.mean()

print("\nDemographic Parity Test for 'typering_other':")
print(adres_risk_scores)


Demographic Parity Test for 'typering_other':
{0.0: 0.05650102110279102, 1.0: 0.06544754571703561, 2.0: 0.09523809523809523}


# Wilcoxon rank-sum test

In [60]:
from scipy.stats import ranksums

# Predict probabilities for the entire dataset
predicted_probabilities = model.predict_proba(X_test)[:, 1]

# Split the predicted probabilities based on gender
female_predicted = predicted_probabilities[X_test['persoon_geslacht_vrouw'] == 1]
male_predicted = predicted_probabilities[X_test['persoon_geslacht_vrouw'] == 0]

# Perform the Wilcoxon rank-sum test
statistic, p_value = ranksums(female_predicted, male_predicted)

print("Wilcoxon Rank-Sum Test:")
print(f"Statistic: {statistic}")
print(f"P-value: {p_value}")


Wilcoxon Rank-Sum Test:
Statistic: -1.851072263315663
P-value: 0.06415915776180084


# Kolmorogov-Smirnov test


In [61]:
print("\nKolmogorov-Smirnov test:")
for i in range(len(age_data)):
    for j in range(i+1, len(age_data)):
        group_i_preds = model.predict(age_data[i])
        group_j_preds = model.predict(age_data[j])
        ks_stat, ks_pval = ks_2samp(group_i_preds, group_j_preds)
        print(f"  Age groups {age_groups[i]}-{age_groups[i+1]} and {age_groups[j]}-{age_groups[j+1]}:")
        print(f"    Statistic: {ks_stat:.4f}, p-value: {ks_pval:.4f}")


Kolmogorov-Smirnov test:
  Age groups 18-26 and 26-36:
    Statistic: 0.0673, p-value: 0.9991
  Age groups 18-26 and 36-46:
    Statistic: 0.1338, p-value: 0.6542
  Age groups 18-26 and 46-56:
    Statistic: 0.2086, p-value: 0.1487
  Age groups 18-26 and 56-66:
    Statistic: 0.2309, p-value: 0.0871
  Age groups 26-36 and 36-46:
    Statistic: 0.0665, p-value: 0.4423
  Age groups 26-36 and 46-56:
    Statistic: 0.1414, p-value: 0.0013
  Age groups 26-36 and 56-66:
    Statistic: 0.1636, p-value: 0.0002
  Age groups 36-46 and 46-56:
    Statistic: 0.0749, p-value: 0.0300
  Age groups 36-46 and 56-66:
    Statistic: 0.0971, p-value: 0.0047
  Age groups 46-56 and 56-66:
    Statistic: 0.0222, p-value: 0.9876


# Fairness analysis

In [62]:
from sklearn.metrics import confusion_matrix
from scipy.spatial.distance import pdist, squareform

def fairness_analysis(X_test, y_pred, sensitive_feature):
    # Reset the indices in X_test
    X_test = X_test.reset_index(drop=True)

    # Group by the sensitive feature
    groups = X_test.groupby(sensitive_feature)

    # Demographic Parity Test
    for name, group in groups:
        y_group = y_pred[group.index]
        positive_prediction_rate = y_group.mean()
        print(f"For group {name}, positive prediction rate: {positive_prediction_rate}")

    # Equalized Odds Test
    for name, group in groups:
        y_group = y_pred[group.index]
        tn, fp, fn, tp = confusion_matrix(group[sensitive_feature], y_group).ravel()
        tpr = tp / (tp + fn + 1e-7)  # Add a small constant to avoid division by zero
        fpr = fp / (fp + tn + 1e-7)  # Add a small constant to avoid division by zero
        print(f"For group {name}, TPR: {tpr}, FPR: {fpr}")

    distances = pdist(X_test, 'euclidean')
    prediction_differences = pdist(y_pred.reshape(-1, 1), 'cityblock')
    correlation = np.corrcoef(distances, prediction_differences)[0, 1]
    print(f"Correlation between distances and prediction differences: {correlation}")

# Call the function
predictions = (model.predict_proba(X_test)[:, 1] > 0.5).astype(int)

In [63]:
fairness_analysis(X_test, predictions, 'persoon_geslacht_vrouw')

For group 0.0, positive prediction rate: 0.06264150943396227
For group 1.0, positive prediction rate: 0.05813953488372093
For group 0.0, TPR: 0.0, FPR: 0.0626415094292346
For group 1.0, TPR: 0.05813953487889206, FPR: 0.0
Correlation between distances and prediction differences: 0.014864042536865634


In [64]:
from sklearn.metrics import precision_score, recall_score

def fairness_analysis_non_binary(X_test, y_test, y_pred, sensitive_feature):
    # Group by the sensitive feature
    groups = X_test.groupby(sensitive_feature)

    # Initialize dictionaries to store the precision and recall for each group
    precision_dict = {}
    recall_dict = {}

    # Calculate precision and recall for each group
    for name, group in groups:
        y_group_test = y_test[group.index]
        y_group_pred = y_pred[group.index]
        precision_dict[name] = precision_score(y_group_test, y_group_pred)
        recall_dict[name] = recall_score(y_group_test, y_group_pred)

    print("Demographic Parity Test:")
    for name, precision in precision_dict.items():
        print(f"For group {name}, positive prediction rate (precision): {precision}")

    print("\nEqual Opportunity Test:")
    for name, recall in recall_dict.items():
        print(f"For group {name}, true positive rate (recall): {recall}")

    print("\nDisparate Impact Test:")
    for name1 in precision_dict:
        for name2 in precision_dict:
            if name1 != name2:
                ratio = precision_dict[name1] / precision_dict[name2]
                print(f"Ratio of positive prediction rates between group {name1} and group {name2}: {ratio}")

In [65]:
# Define the age bins and labels
bins = [18, 26, 36, 46, 56, 66]
labels = [1, 2, 3, 4, 5]

# Create a copy of X_test and reset its index
X_test_copy = X_test.copy().reset_index(drop=True)

# Replace the 'persoon_leeftijd_bij_onderzoek' column in the copy
X_test_copy['persoon_leeftijd_bij_onderzoek'] = pd.cut(X_test['persoon_leeftijd_bij_onderzoek'], bins=bins, labels=labels, right=False)

# Call the fairness analysis function with the new feature
fairness_analysis_non_binary(X_test_copy, y_test, predictions, 'persoon_leeftijd_bij_onderzoek')

Demographic Parity Test:
For group 1, positive prediction rate (precision): 1.0
For group 2, positive prediction rate (precision): 0.7948717948717948
For group 3, positive prediction rate (precision): 0.8307692307692308
For group 4, positive prediction rate (precision): 0.8064516129032258
For group 5, positive prediction rate (precision): 0.7142857142857143

Equal Opportunity Test:
For group 1, true positive rate (recall): 0.6363636363636364
For group 2, true positive rate (recall): 0.7045454545454546
For group 3, true positive rate (recall): 0.6067415730337079
For group 4, true positive rate (recall): 0.4098360655737705
For group 5, true positive rate (recall): 0.18518518518518517

Disparate Impact Test:
Ratio of positive prediction rates between group 1 and group 2: 1.2580645161290323
Ratio of positive prediction rates between group 1 and group 3: 1.2037037037037037
Ratio of positive prediction rates between group 1 and group 4: 1.24
Ratio of positive prediction rates between group 1

C:\Users\alexd\AppData\Local\Temp\ipykernel_26128\3024323882.py:5: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  groups = X_test.groupby(sensitive_feature)


# Metamorphic Tests

In [66]:
# Flip the gender binary values
X_test_copy = X_test.copy()
X_test['persoon_geslacht_vrouw'] = 1.0 - X_test['persoon_geslacht_vrouw']
# Evaluate the model
y_pred = model.predict(X_test)
original_accuracy = accuracy_score(y_test, y_pred)
print(classification_report(y_test, y_pred))
print('Accuracy of the original model: ', original_accuracy)
X_test = X_test_copy.copy()

              precision    recall  f1-score   support

           0       0.95      0.99      0.97      2278
           1       0.82      0.50      0.62       251

    accuracy                           0.94      2529
   macro avg       0.89      0.75      0.80      2529
weighted avg       0.94      0.94      0.93      2529

Accuracy of the original model:  0.9398971925662317


In [67]:
# Flip the language binary values
X_test['persoonlijke_eigenschappen_taaleis_voldaan'] = 1.0 - X_test['persoonlijke_eigenschappen_taaleis_voldaan']
# Evaluate the model
y_pred = model.predict(X_test)
original_accuracy = accuracy_score(y_test, y_pred)
print(classification_report(y_test, y_pred))
print('Accuracy of the original model: ', original_accuracy)
X_test = X_test_copy.copy()

              precision    recall  f1-score   support

           0       0.95      0.99      0.97      2278
           1       0.84      0.51      0.63       251

    accuracy                           0.94      2529
   macro avg       0.89      0.75      0.80      2529
weighted avg       0.94      0.94      0.93      2529

Accuracy of the original model:  0.941083432186635


In [68]:
# Flip the gender binary values
X_test['deelname_act_reintegratieladder_werk_re_integratie'] = 1.0 - X_test['deelname_act_reintegratieladder_werk_re_integratie']
# Evaluate the model
y_pred = model.predict(X_test)
original_accuracy = accuracy_score(y_test, y_pred)
print(classification_report(y_test, y_pred))
print('Accuracy of the original model: ', original_accuracy)

              precision    recall  f1-score   support

           0       0.95      0.99      0.97      2278
           1       0.84      0.50      0.62       251

    accuracy                           0.94      2529
   macro avg       0.89      0.74      0.80      2529
weighted avg       0.94      0.94      0.93      2529

Accuracy of the original model:  0.9406880189798339
